# Importando bibliotecas

In [ ]:
import csv
import pandas as pd
import re
import nltk
import spacy
from sklearn.feature_extraction.text import TfidfVectorizer

import nltk
nltk.download('stopwords')
nltk.download('punkt')

from sklearn.manifold import TSNE
import umap.umap_ as umap
import plotly.express as px

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

# Importando conjunto de dados

In [ ]:
df = pd.read_csv("discursos_selecionados.csv")
df

Discurso  ... presidente
0      O SR. PAULO PAIM (Bloco/PT - RS. Pronuncia o s...  ...      Dilma
1      O SR. JAYME CAMPOS (Bloco Minoria/DEM - MT. Pr...  ...      Dilma
2      O SR. LASIER MARTINS  (Bloco Parlamentar Democ...  ...      Temer
3      O SR. ALVARO DIAS (PSDB - PR. Pela ordem. Sem ...  ...       Lula
4      O SR. PAULO PAIM (Bloco/PT- RS. Pronuncia o se...  ...      Dilma
...                                                  ...  ...        ...
11217  A SRA. ZENAIDE MAIA  (Bloco Parlamentar da Res...  ...  Bolsonaro
11218  O SR. CIRO NOGUEIRA (Bloco/PP - PI. Pronuncia ...  ...      Dilma
11219  O SR. PAULO PAIM  (Bloco Parlamentar da Resist...  ...  Bolsonaro
11220  O SR. ACIR GURGACZ  (Bloco Parlamentar Senado ...  ...  Bolsonaro
11221  O SR. ALVARO DIAS (Bloco/PSDB - PR. Pronuncia ...  ...      Dilma

[11222 rows x 9 columns]

# Normalização do texto

In [ ]:
def cleanText(text):
    text = text.lower()
    text = re.sub(r"á", "a", text)
    text = re.sub(r"â", "a", text)
    text = re.sub(r"à", "a", text)
    text = re.sub(r"ã", "a", text)
    text = re.sub(r"é", "e", text)
    text = re.sub(r"ê", "e", text)
    text = re.sub(r"í", "i", text)
    text = re.sub(r"ó", "o", text)
    text = re.sub(r"ô", "o", text)
    text = re.sub(r"õ", "o", text)
    text = re.sub(r"ú", "u", text)
    text = re.sub(r"ç", "c", text)
    text = re.sub(r"[^a-zA-Z ]", "", text)
    text = re.sub(r"\\W", "", text)
    text = re.sub(r"\\s+", "", text)
    text = text.strip(' ')
    return text

text = df['Discurso'].map(lambda com: cleanText(com))
text[0]

'o sr paulo paim blocopt  rs pronuncia o seguinte discurso sem revisao do orador  senador mozarildo cavalcanti que preside a sessao senador fernando collor de mello que usou a tribuna antes deste orador eu quero fazer aqui dois registros sr presidente e depois quero fazer uma analise mais detalhada da importancia da aprovacao pelo senado e pela camara de um projeto dos autistas e a analise eu farei mediante uma carta que recebi da principal lider eu diria dos autistas do pais que me encaminhou essa carta esta semana a sr berenice piana de piana primeiro os dois registros quero dizer que hoje a noite estarei no hotel sao marco aqui em brasilia participando da solenidade de posse da nova diretoria da contratuh eleita para o quinquenio de  de dezembro de  a  de dezembro de  moacyr roberto tesch o atual presidente dessa confederacao ativo e participante foi reeleito para a presidencia dessa confederacao inclusive quando convidado esteve aqui no congresso nacional dezenas e dezenas de vezes

# Remoção de stop-words

In [ ]:
stop_list = nltk.corpus.stopwords.words('portuguese')

text_tokens = [nltk.word_tokenize(doc) for doc in text]

def remove_stopwords(tokens):
    return [token for token in tokens if token.lower() not in stop_list]  

text_stop = [' '.join(remove_stopwords(doc)) for doc in text_tokens]

text_stop[0]

'sr paulo paim blocopt rs pronuncia seguinte discurso revisao orador senador mozarildo cavalcanti preside sessao senador fernando collor mello usou tribuna antes deste orador quero fazer aqui dois registros sr presidente quero fazer analise detalhada importancia aprovacao senado camara projeto autistas analise farei mediante carta recebi principal lider diria autistas pais encaminhou carta semana sr berenice piana piana primeiro dois registros quero dizer hoje noite estarei hotel sao marco aqui brasilia participando solenidade posse nova diretoria contratuh eleita quinquenio dezembro dezembro moacyr roberto tesch atual presidente dessa confederacao ativo participante reeleito presidencia dessa confederacao inclusive convidado aqui congresso nacional dezenas dezenas vezes durante ano partir dia dezembro confederacao deu inicio aqui brasilia congresso nacional trabalhadores turismo hospitalidade dirigentes sindicais participam evento objetivo definir bandeiras contratuh vai defender cont

In [ ]:
df['text'] = text_stop
df['text'][0]

'sr paulo paim blocopt rs pronuncia seguinte discurso revisao orador senador mozarildo cavalcanti preside sessao senador fernando collor mello usou tribuna antes deste orador quero fazer aqui dois registros sr presidente quero fazer analise detalhada importancia aprovacao senado camara projeto autistas analise farei mediante carta recebi principal lider diria autistas pais encaminhou carta semana sr berenice piana piana primeiro dois registros quero dizer hoje noite estarei hotel sao marco aqui brasilia participando solenidade posse nova diretoria contratuh eleita quinquenio dezembro dezembro moacyr roberto tesch atual presidente dessa confederacao ativo participante reeleito presidencia dessa confederacao inclusive convidado aqui congresso nacional dezenas dezenas vezes durante ano partir dia dezembro confederacao deu inicio aqui brasilia congresso nacional trabalhadores turismo hospitalidade dirigentes sindicais participam evento objetivo definir bandeiras contratuh vai defender cont

# TF-IDF

In [ ]:
corpus = list(df.text)
tfidf = TfidfVectorizer() 
tfidf.fit(corpus)
tfidf_result = tfidf.transform(corpus)
print(tfidf_result.shape)

(11222, 123334)


# t-SNE

In [ ]:
tsne = TSNE(perplexity=100,learning_rate=100)

tsne_results = tsne.fit_transform(tfidf_result)

df_tsne = pd.DataFrame(tsne_results, columns=["x", "y"])

df_tsne 

x          y
0     -29.328539  15.604312
1     -32.198784  30.894821
2      20.759207   0.971402
3       4.545074 -41.534546
4     -24.681171  19.162708
...          ...        ...
11217   3.298386  11.326302
11218 -10.373796  17.647995
11219   8.707013  13.669740
11220  -6.027068  40.221622
11221 -50.106529  32.184135

[11222 rows x 2 columns]

In [ ]:

df_tsne['Discurso'] = df.Discurso
df_tsne['NomeParlamentar'] = df.NomeParlamentar
df_tsne['NomeCompletoParlamentar'] = df.NomeCompletoParlamentar
df_tsne['SexoParlamentar'] = df.SexoParlamentar

df_tsne['SiglaPartidoParlamentar'] = df.SiglaPartidoParlamentar

df_tsne['UfParlamentar'] = df.UfParlamentar
df_tsne['TextoResumo'] = df.TextoResumo
df_tsne['DataPronunciamento'] = df.DataPronunciamento
df_tsne['presidente'] = df.presidente

df_tsne

x          y  ... DataPronunciamento presidente
0     -29.328539  15.604312  ...         2012-12-07      Dilma
1     -32.198784  30.894821  ...         2014-11-18      Dilma
2      20.759207   0.971402  ...         2018-08-08      Temer
3       4.545074 -41.534546  ...         2007-10-03       Lula
4     -24.681171  19.162708  ...         2011-10-17      Dilma
...          ...        ...  ...                ...        ...
11217   3.298386  11.326302  ...         2019-09-11  Bolsonaro
11218 -10.373796  17.647995  ...         2013-04-15      Dilma
11219   8.707013  13.669740  ...         2019-11-06  Bolsonaro
11220  -6.027068  40.221622  ...         2019-07-05  Bolsonaro
11221 -50.106529  32.184135  ...         2012-06-19      Dilma

[11222 rows x 11 columns]

In [ ]:
#df_tsne.to_csv("discursos_tsne.csv", index=False)

In [ ]:
#df_tsne_30 = df_tsne
figure = px.scatter(df_tsne_30, x='x', y='y',color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
#df_tsne_50 = df_tsne
figure = px.scatter(df_tsne_50, x='x', y='y',color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
#df_tsne_100 = df_tsne
figure = px.scatter(df_tsne_100, x='x', y='y',color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
df_tsne_100_100 = df_tsne
figure = px.scatter(df_tsne_100_100, x='x', y='y',color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

# UMAP

In [ ]:
reducer = umap.UMAP(n_neighbors=100, min_dist=0.8,metric='euclidean')
embedding = reducer.fit_transform(tfidf_result)


x = list(embedding[:,0])
y = list(embedding[:,1])

df_umap = pd.DataFrame(x, columns=["x"])

df_umap['y'] = y

df_umap

x         y
0      10.257933 -4.513885
1      13.802954 -2.612756
2       6.550318 -2.318504
3       5.709419  2.190668
4      10.956658 -2.705526
...          ...       ...
11217   5.835804 -4.854722
11218  10.366483 -1.953275
11219   6.000105 -4.419797
11220  10.323307  2.875732
11221   8.161466 -1.975085

[11222 rows x 2 columns]

In [ ]:
#df_umap['Discurso'] = df.Discurso
df_umap['NomeParlamentar'] = df.NomeParlamentar
#df_umap['NomeCompletoParlamentar'] = df.NomeCompletoParlamentar
#df_umap['SexoParlamentar'] = df.SexoParlamentar
df_umap['SiglaPartidoParlamentar'] = df.SiglaPartidoParlamentar
df_umap['UfParlamentar'] = df.UfParlamentar
#df_umap['TextoResumo'] = df.TextoResumo
#df_umap['DataPronunciamento'] = df.DataPronunciamento
df_umap['presidente'] = df.presidente
df_umap

x         y  ... UfParlamentar presidente
0      10.257933 -4.513885  ...            RS      Dilma
1      13.802954 -2.612756  ...            MT      Dilma
2       6.550318 -2.318504  ...            RS      Temer
3       5.709419  2.190668  ...            PR       Lula
4      10.956658 -2.705526  ...            RS      Dilma
...          ...       ...  ...           ...        ...
11217   5.835804 -4.854722  ...            RN  Bolsonaro
11218  10.366483 -1.953275  ...            PI      Dilma
11219   6.000105 -4.419797  ...            RS  Bolsonaro
11220  10.323307  2.875732  ...            RO  Bolsonaro
11221   8.161466 -1.975085  ...            PR      Dilma

[11222 rows x 6 columns]

In [ ]:
#df_umap_15 = df_umap
figure = px.scatter(df_umap_15, x='x', y='y', color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
df_umap_15_05 = df_umap
figure = px.scatter(df_umap_15_05, x='x', y='y', color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
df_umap_50 = df_umap
figure = px.scatter(df_umap_50, x='x', y='y', color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
df_umap_100 = df_umap
figure = px.scatter(df_umap, x='x', y='y', color = "NomeParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
figure = px.scatter(df_umap, x='x', y='y', color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
figure = px.scatter(df_umap, x='x', y='y', color = "presidente", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

figure.update_layout(showlegend=False)

In [ ]:
df_umap.to_csv("discursos_umap.csv", index=False)

# Organizando o resultado final em um arquivo csv

In [ ]:
df_final = pd.DataFrame()
df_final['x_tsne'] = df_tsne.x
df_final['y_tsne'] = df_tsne.y
df_final['x_umap'] = df_umap.x
df_final['y_umap'] = df_umap.y
df_final['Discurso'] = df.Discurso
df_final['NomeParlamentar'] = df.NomeParlamentar
df_final['NomeCompletoParlamentar'] = df.NomeCompletoParlamentar
df_final['SexoParlamentar'] = df.SexoParlamentar
df_final['SiglaPartidoParlamentar'] = df.SiglaPartidoParlamentar
df_final['UfParlamentar'] = df.UfParlamentar
df_final['TextoResumo'] = df.TextoResumo
df_final['DataPronunciamento'] = df.DataPronunciamento
df_final['presidente'] = df.presidente
df_final

x_tsne     y_tsne  ...  DataPronunciamento  presidente
0     -29.328539  15.604312  ...          2012-12-07       Dilma
1     -32.198784  30.894821  ...          2014-11-18       Dilma
2      20.759207   0.971402  ...          2018-08-08       Temer
3       4.545074 -41.534546  ...          2007-10-03        Lula
4     -24.681171  19.162708  ...          2011-10-17       Dilma
...          ...        ...  ...                 ...         ...
11217   3.298386  11.326302  ...          2019-09-11   Bolsonaro
11218 -10.373796  17.647995  ...          2013-04-15       Dilma
11219   8.707013  13.669740  ...          2019-11-06   Bolsonaro
11220  -6.027068  40.221622  ...          2019-07-05   Bolsonaro
11221 -50.106529  32.184135  ...          2012-06-19       Dilma

[11222 rows x 13 columns]

In [ ]:
figure = px.scatter(df_final, x='x_tsne', y='y_tsne', color = "presidente", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

#figure.update_layout(showlegend=False)

In [ ]:
figure = px.scatter(df_final, x='x_umap', y='y_umap', color = "SiglaPartidoParlamentar", color_discrete_sequence=px.colors.qualitative.Pastel)

figure.update_traces(marker=dict(line=dict(width=1, color='white')))

#figure.update_layout(showlegend=False)

In [ ]:
df_final.to_csv("discursos_final.csv", index=False)